In [ ]:
!pip install -q wandb torchmetrics

     |████████████████████████████████| 1.7 MB 13.7 MB/s 
     |████████████████████████████████| 398 kB 59.5 MB/s 
     |████████████████████████████████| 181 kB 65.8 MB/s 
     |████████████████████████████████| 144 kB 40.8 MB/s 
     |████████████████████████████████| 63 kB 1.9 MB/s 


In [ ]:
!wget https://ai.tencent.com/ailab/nlp/en/data/tencent-ailab-embedding-zh-d200-v0.2.0-s.tar.gz

--2022-04-03 04:09:21--  https://ai.tencent.com/ailab/nlp/en/data/tencent-ailab-embedding-zh-d200-v0.2.0-s.tar.gz
Resolving ai.tencent.com (ai.tencent.com)... 116.128.164.87
Connecting to ai.tencent.com (ai.tencent.com)|116.128.164.87|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1544075399 (1.4G) [application/octet-stream]
Saving to: ‘tencent-ailab-embedding-zh-d200-v0.2.0-s.tar.gz’

tencent-ailab-embed 100%[===================>]   1.44G  58.6MB/s    in 67s     

2022-04-03 04:10:28 (21.9 MB/s) - ‘tencent-ailab-embedding-zh-d200-v0.2.0-s.tar.gz’ saved [1544075399/1544075399]



In [ ]:
import pickle
import random
import pytz
from datetime import datetime
import numpy as np
from tqdm.auto import tqdm

import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader

In [ ]:
import wandb
wandb.login()

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

## Preprocessing Embeddings

In [ ]:
import gzip
import tarfile
with gzip.open("tencent-ailab-embedding-zh-d200-v0.2.0-s.tar.gz", "r") as gopen:
  tar = tarfile.open(fileobj=gopen)
  tar.next()
  tinfo = tar.next()
  fin = tar.extractfile(tinfo)  
  nvocab, hdim = fin.readline().split()
  # N = int(nvocab)
  N = 500_000
  embs = np.zeros((N, int(hdim)))
  vocabs = [""] * N
  counter = 0

  for i in tqdm(range(N)):    
    ln = fin.readline().decode().strip()    
    if not ln: continue    
    toks = ln.split(" ")
    if len(toks[0]) > 2: continue
    vocabs[counter] = toks[0]
    embs[counter, :] = [float(x) for x in toks[1:]]
    counter += 1
embs = embs[:counter, :]
vocabs = vocabs[:counter]
embs = embs / np.linalg.norm(embs, axis=1)[:, np.newaxis]

  0%|          | 0/500000 [00:00<?, ?it/s]

In [ ]:
sum(1 for x in vocabs if len(x)==1), sum(1 for x in vocabs if len(x)==2)

(7954, 121584)

In [ ]:
## write used embeddings to pickle
# with open("drive/MyDrive/LangOn/convmorph/convmorph_dataset.pkl", "wb") as fout:
#   pickle.dump((vocabs, embs), fout)

In [ ]:
with open("drive/MyDrive/LangOn/convmorph/convmorph_dataset.pkl", "rb") as fin:
  (vocabs, embs) = pickle.load(fin)

In [ ]:
class ConvmorphDataset(Dataset):
  def __init__(self, vocabs, embs):
    self.build_dataset(vocabs, embs)

  def build_dataset(self, vocabs, embs):
    vocab_map = {vocab: idx for idx, vocab in enumerate(vocabs)}
    self.data = []
    for idx in tqdm(range(len(vocabs)), desc="building dataset"):
      word = vocabs[idx]
      if len(word) < 2: continue
      if not (word[0] in vocab_map and word[1] in vocab_map):
        continue
      emb = embs[idx]
      const1_vec = embs[vocab_map[word[0]]]
      const2_vec = embs[vocab_map[word[1]]]
      const1 = word[0]
      const2 = word[1]
      self.data.append(dict(
          word=word,
          const1=const1, const2=const2,
          word_vec=emb,
          const1_vec=const1_vec, const2_vec=const2_vec
      ))
  
  def __len__(self):
    return len(self.data)

  def __getitem__(self, idx):
    return self.data[idx]

In [ ]:
cm_ds = ConvmorphDataset(vocabs, embs)
len(cm_ds)

building dataset:   0%|          | 0/129538 [00:00<?, ?it/s]

120838

In [ ]:
np.concatenate([cm_ds[0]["const1_vec"], cm_ds[0]["const2_vec"]]).reshape(20,20).shape

(20, 20)

In [ ]:
class ConvmorphDatasetArc(Dataset):
  def __init__(self, cm_dataset, idxs):
    self.build_dataset(cm_dataset, idxs)

  def build_dataset(self, ds, idxs):
    self.data = []
    for serial, idx in enumerate(idxs):
      data_x = ds[idx]
      inputX = np.concatenate([
          data_x["const1_vec"], data_x["const2_vec"]
      ]).reshape(1, 20, 20)
      target = data_x["word_vec"]
      self.data.append(dict(
          word_id=serial,
          inputX=torch.tensor(inputX, dtype=torch.float32),
          target=torch.tensor(target, dtype=torch.float32)
      ))
  
  def __len__(self):
    return len(self.data)

  def __getitem__(self, idx):
    return self.data[idx]


In [ ]:
N = len(cm_ds)
rng = np.random.RandomState(123)
random_split = np.arange(N)
rng.shuffle(random_split)
train_idxs = random_split[:int(N*.95)]
test_idxs = random_split[int(N*.95):]
train_ds = ConvmorphDatasetArc(cm_ds, train_idxs)
test_ds = ConvmorphDatasetArc(cm_ds, test_idxs)
train_eval_ds = ConvmorphDatasetArc(cm_ds, train_idxs[-len(test_ds):])
print(len(train_idxs), len(test_idxs), len(train_eval_ds))

114796 6042 6042


In [ ]:
with open("drive/MyDrive/LangOn/convmorph/split_inidices_120k.pkl", "wb") as fout:
  pickle.dump({"train_idxs": train_idxs, "test_idxs": test_idxs}, fout)

## Prepare Dataset

In [ ]:
from dataclasses import dataclass
import torch.nn.functional as F

@dataclass
class ConvmorphArcModelOutput:
  loss: torch.tensor
  pred_vec: torch.tensor

class ConvmorphArcModel(nn.Module):
  def __init__(self, dropout=0.1):
    super().__init__()

    self.conv1 = nn.Conv2d(1, 128, 3)
    self.norm1 = nn.LayerNorm([128, 18, 18])
    self.conv2 = nn.Conv2d(128, 128, 3)
    self.norm2 = nn.LayerNorm([128, 16, 16])    
    self.conv3 = nn.Conv2d(128, 128, 3)
    self.norm3 = nn.LayerNorm([128, 14, 14])    
    self.conv4 = nn.Conv2d(128, 128, 3)
    self.norm4 = nn.LayerNorm([128, 12, 12])
    self.conv5 = nn.Conv2d(128, 128, 3)
    self.norm5 = nn.LayerNorm([128, 10, 10])
    
    self.pool1 = nn.MaxPool2d(2)
    self.fn1 = nn.Linear(128*5*5, 3000)
    self.drop1 = nn.Dropout(p=dropout)
    # self.fn2 = nn.Linear(512, 200)   
    # self.fn2 = nn.Linear(2048, 1024)
    # self.drop2 = nn.Dropout(p=dropout)
    # self.fn3 = nn.Linear(1024, 512)
    # self.drop3 = nn.Dropout(p=dropout)
    # self.fn4 = nn.Linear(512, 200)
    self.fn4 = nn.Linear(3000, 200)
  
  def forward(self, inputX, target=None, **kwargs):
    
    z = F.relu(self.norm1(self.conv1(inputX)), inplace=True)
    z = F.relu(self.norm2(self.conv2(z)), inplace=True)
    z = F.relu(self.norm3(self.conv3(z)), inplace=True)
    z = F.relu(self.norm4(self.conv4(z)), inplace=True)    
    z = F.relu(self.norm5(self.conv5(z)), inplace=True)    
    z = self.pool1(z).view(-1, 128*5*5)
    o = self.drop1(torch.tanh(self.fn1(z)))    
    # o = self.drop2(torch.tanh(self.fn2(o)))
    # o = self.drop3(torch.tanh(self.fn3(o)))
    o = self.fn4(o)
    pred_vec = o

    if target is not None:
      loss_fct = nn.MSELoss()
      loss = loss_fct(pred_vec, target)
      return ConvmorphArcModelOutput(loss, pred_vec)
    else:      
      return ConvmorphArcModelOutput(float('nan'), pred_vec)
    

In [ ]:
def compute_accuracy(data_loader, test_embs):
  n_correct = 0
  n_items = 0
  model.eval()
  for batch_x in tqdm(data_loader):
      with torch.no_grad():
        batch_x = {k: v.to("cuda") for k, v in batch_x.items()}
        word_ids = batch_x["word_id"].cpu().numpy()
        pred_vec = model(**batch_x).pred_vec      
        preds = torch.argmax(torch.matmul(pred_vec, test_embs.transpose(1, 0)), dim=1).cpu().numpy()
        n_correct += np.array(word_ids==preds, dtype=np.int32).sum()
        n_items += len(preds)
  return n_correct/n_items

In [ ]:
from torch.optim.lr_scheduler import LambdaLR
# From https://github.com/huggingface/transformers/blob/v4.17.0/src/transformers/optimization.py
def get_linear_schedule_with_warmup(optimizer, num_warmup_steps, num_training_steps, last_epoch=-1):    
    def lr_lambda(current_step: int):
        if current_step < num_warmup_steps:
            return float(current_step) / float(max(1, num_warmup_steps))
        return max(
            0.0, float(num_training_steps - current_step) / float(max(1, num_training_steps - num_warmup_steps))
        )

    return LambdaLR(optimizer, lr_lambda, last_epoch)

In [ ]:
eval_embs = torch.tensor(np.vstack([x["target"] for x in test_ds]), dtype=torch.float32).to("cuda")
train_eval_embs = torch.tensor(np.vstack([x["target"] for x in train_eval_ds]), dtype=torch.float32).to("cuda")

In [ ]:
config = dict(
    lr=5e-4,
    scheduler="linear",
    batch_size=128,
    epochs=300,
    dropout=0.1,
    note='128x5x5->fn:3000,200'
)

run_name = datetime.now(pytz.timezone('Asia/Taipei')).strftime("%m%d-%H%M-arc")
wandb.init(project="convmorph", name=run_name, config=config, save_code=True)

wandb: Currently logged in as: seantyh (use `wandb login --relogin` to force relogin)


In [ ]:
from itertools import islice
epochs = config["epochs"]
lr = config["lr"]
batch_size = config["batch_size"]

##   Dataset
## -----------
train_loader = DataLoader(train_ds, batch_size=batch_size, shuffle=True)
eval_loader = DataLoader(test_ds, batch_size=batch_size, shuffle=False)

##    Model
## ----------
model = ConvmorphArcModel(dropout=config["dropout"]).to("cuda")
optimizer = optim.AdamW(model.parameters(), lr=lr)
total_steps = epochs*len(train_loader)
scheduler = get_linear_schedule_with_warmup(optimizer, 0, total_steps)

torch.backends.cudnn.deterministic = True
torch.manual_seed(123)
random.seed(123)

train_eploss_vec = []
eval_eploss_vec = []

iter_counter = 0
pbar = tqdm(total=total_steps)
for epoch_i in range(epochs):
  train_loss_vec = []
  eval_loss_vec = []
  model.train()  
  pbar.set_description(f"Epoch {epoch_i}/Train")
  for batch_x in train_loader:
    pbar.update(1)
    optimizer.zero_grad()  
    batch_x = {k: v.to("cuda") for k, v in batch_x.items()}
    loss = model(**batch_x).loss
    loss.backward()
    optimizer.step()
    scheduler.step()
    train_loss_vec.append(loss.item())    
    if iter_counter % 100 == 0:
      wandb.log({"train/loss": loss.item()}, step=iter_counter)
    iter_counter += 1
  train_eploss_vec.append(np.mean(train_loss_vec))  

  pbar.set_description(f"Epoch {epoch_i}/Eval")
  for batch_x in eval_loader:
    model.eval()
    with torch.no_grad():
      batch_x = {k: v.to("cuda") for k, v in batch_x.items()}
      loss = model(**batch_x).loss
      eval_loss_vec.append(loss.item())    
  eval_eploss_vec.append(np.mean(eval_loss_vec))  
  train_acc = compute_accuracy(DataLoader(train_eval_ds, batch_size=128, shuffle=False), train_eval_embs)
  test_acc = compute_accuracy(DataLoader(test_ds, batch_size=128, shuffle=False), eval_embs)
  wandb.log({
      "train/epoch-loss": train_eploss_vec[-1],
      "eval/epoch-loss": eval_eploss_vec[-1],
      "eval/train-acc": train_acc,
      "eval/test-acc": test_acc,
      "trainer/lr": scheduler.get_last_lr()[0]
  }, step=iter_counter)
  print(f"train/eval loss: {train_eploss_vec[-1]}/{eval_eploss_vec[-1]}")
wandb.finish()
pbar.close()

  0%|          | 0/48 [00:00<?, ?it/s]

  0%|          | 0/48 [00:00<?, ?it/s]

train/eval loss: 0.002640987353434697/0.0028080627331898236


  0%|          | 0/48 [00:00<?, ?it/s]

  0%|          | 0/48 [00:00<?, ?it/s]

...

  0%|          | 0/48 [00:00<?, ?it/s]

train/eval loss: 0.001954571192242089/0.0030147410046386844


  0%|          | 0/48 [00:00<?, ?it/s]

  0%|          | 0/48 [00:00<?, ?it/s]

train/eval loss: 0.001953416206762859/0.003014550073809611



In [ ]:
import os
out_dir = "drive/MyDrive/LangOn/convmorph/" + run_name
os.makedirs(out_dir, exist_ok=True)
torch.save(model.state_dict(), out_dir+"/model.pth")